In [67]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime

from sklearn.metrics.pairwise import linear_kernel
from sklearn.metrics import pairwise_distances
from sklearn.model_selection import train_test_split, LeaveOneOut
from surprise.model_selection import train_test_split as tts
from scipy.spatial.distance import cosine, correlation
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import MinMaxScaler

import tensorflow as tf
from scipy import sparse
import pickle


In [68]:
os.listdir('../Modeling')

['.ipynb_checkpoints',
 '1 - Modeling Surprise.ipynb',
 '2 Opt - TFRS Playground (compare TFRS models) (Optional).ipynb',
 '3 - TFRS Final.ipynb',
 'models']

In [69]:
pickles = ['SVD_one_to_five.sav', 'SVD_negone_to_one.sav', 
           'SVD++_one_to_five.sav', 'SVD++_negone_to_one.sav']

# open a file, where you stored the pickled data
file = open('../Modeling/models/SVD_one_to_five.sav', 'rb')

# dump information to that file
SVDone_to_five = pickle.load(file)

# close the file
file.close()

In [70]:
file = open('../Modeling/models/SVD_negone_to_one.sav', 'rb')
SVD_negone_to_one = pickle.load(file)
file.close()

file = open('../Modeling/models/SVD++_one_to_five.sav', 'rb')
SVDpp_one_to_five = pickle.load(file)
file.close()

file = open('../Modeling/models/SVD++_negone_to_one.sav', 'rb')
SVDpp_negone_to_one = pickle.load(file)
file.close()

algos = [SVDone_to_five, SVD_negone_to_one, SVDpp_one_to_five, SVDpp_negone_to_one]

In [71]:
#dlModels
#set location
path = os.path.join('../Modeling/models', "adaOhOneModel")

# Load it back; can also be done in TensorFlow Serving.
adaModel = tf.keras.models.load_model(path)

path = os.path.join('../Modeling/models', "adamOhOhOneModel")
adamModel = tf.keras.models.load_model(path)

In [72]:
popularityTable = pd.read_csv('../../Data/popularity_table.csv', index_col=[0])
popRatings = pd.read_csv('../../Data/popularity_ratings.csv', index_col=[0])

In [73]:
movies = pd.read_csv('../../Data/movies_processed.csv', index_col=[0])#, parse_dates=['year'])
ratings = pd.read_csv('../../Data/ratings_processed.csv', index_col=[0])#, parse_dates=['timestamp'])
#moviesWithRaw = pd.read_csv('../../Data/movies_with_raw.csv', index_col=[0])

In [74]:
movies = movies[movies.movieId.isin(ratings.movieId)]

In [75]:
movie_based_similarity = pd.read_csv('../../Data/movie_cosine_similarity.csv', index_col=[0])
movie_based_similarity.index = movies.movieId
movie_based_similarity.columns = movies.movieId
user_based_similarity = pd.read_csv('../../Data/user_cosine_similarity.csv', index_col=[0])
user_based_similarity.index = ratings.userId.unique()
user_based_similarity.columns = ratings.userId.unique()

In [76]:
similarities = pd.read_csv('../../Data/cos_sim_id.csv', index_col=[0])
#similaritiesWithNames = pd.read_csv('../../cos_sim_names.csv', index_col=[0])

In [77]:
recents = movies[movies.year == 2018]

In [78]:
#mov = pd.read_csv('tfmovs.csv', index_col=[0])
#rat = pd.read_csv('tfratings.csv', index_col=[0])

In [79]:
def last_movie(usrId):
    df = ratings[ratings.userId == usrId].sort_values('timestamp')
    last = pd.DataFrame(df.iloc[-1]).T.merge(movies[['movieId', 'title']], on='movieId')
    return last

In [80]:
def cos_sim_preds(usrId, limit:int=None):
    df = last_movie(usrId)
    ID = df.movieId[0]
    
    output = similarities.loc[ID].sort_values(ascending=False)
    if limit is not None:
        output = output[:limit]
    output.index = output.index.astype('int')
    
    return output

In [81]:
def user_rated(usrId):
    rated = ratings[ratings.userId == usrId].merge(
        movies[['movieId', 'title']], on='movieId')[['title', 'movieId']].set_index('title')
    return rated

In [82]:
def cos_sim_hitrate(usrId, HR_limit=20):
    preds = cos_sim_preds(usrId)[:HR_limit]
    rated = user_rated(usrId)
    
    rated.reset_index(inplace=True)
    
    mask = preds.index.isin(rated.movieId)
    display(preds[mask])
    
    return mask.sum()

In [83]:
def rec_movie(movie_id, moviedf=movies, limit=20):
    temp_table = pd.DataFrame(columns = moviedf.columns)
    movies = movie_based_similarity[movie_id].sort_values(ascending = False).index.tolist()[:limit]
    for mov in movies:
#         display(items[items['movie id'] == mov])
        temp_table = temp_table.append(moviedf[moviedf['movieId'] == mov], ignore_index=True)
    return temp_table
def rec_user(user_id, ratingdf=ratings):
    temp_table = pd.DataFrame(columns = ratings.columns)
    us = user_based_similarity[user_id].sort_values(ascending = False).index.tolist()[:101]
    for u in us:
#         display(items[items['movie id'] == mov])
        temp_table = temp_table.append(ratingdf[ratingdf['userId'] == u], ignore_index=True)
    return temp_table

In [84]:
def movieCF_preds(usrId):
    userCF = rec_movie(last_movie(usrId).movieId[0])
    return userCF

In [85]:
def movieCF_hitrate(usrId, HR_limit=20):
    userCF = movieCF_preds(usrId)
    userCF = userCF[userCF.movieId != last_movie(usrId).movieId[0]]
    
    if userCF.shape[0] > HR_limit:
        userCF = userCF[:HR_limit]
    
    mask = userCF.movieId.isin(user_rated(80).movieId)

    hrstring = 'Hitrate @'+str(HR_limit)+' is: '+str(mask.sum())
    recShape = str(len(userCF))+' recs generated'
    titlesMatched = 'Movies Matched: '+userCF[mask].title.values
    
    print(hrstring+'; '+recShape+'; '+titlesMatched)
    return mask.sum() 

In [86]:
def algo_preds(algo, usrId, limit:int=None):
    preds = []
    
    for i in movies.movieId.unique():    
        preds.append(algo.predict(usrId, i))
    
    preds = pd.DataFrame(preds).sort_values('est', ascending=False)  
    
    if limit is not None:
        preds = preds[:limit]
        
    preds = preds.merge(movies[['movieId', 'title']], left_on='iid', right_on='movieId')
    preds.drop(['r_ui', 'details'], axis=1, inplace=True)
    preds['rank'] = preds.est.rank(ascending=False)
    
    return preds

In [87]:
def algo_hitrate(algo, usrId, HR_limit=20):
    preds = algo_preds(algo, usrId, HR_limit)
    rated = user_rated(usrId).movieId
    
    mask = preds.movieId.isin(rated)
    merged = preds[mask].merge(ratings[['userId', 'movieId', 'rating']], 
                                       left_on=['uid', 'iid'], right_on=['userId', 'movieId'])
    display(merged)
    return mask.sum()

In [88]:
def dl_preds(algo, usrId, movie_df=movies):
    scores, titles = algo([str(usrId)])
    titles = titles.numpy()
    titles_processed = []
    
    for i in range(len(titles[0])):
        tit = titles[0][i].decode('utf-8')
        titles_processed.append(tit)

    titles_processed = pd.DataFrame(titles_processed, 
                                    columns=['title']
                                   ).merge(movie_df[['movieId', 'title']],
                                           on='title')
    
    return titles_processed

In [89]:
def dl_hitrate(algo, usrId, HR_limit=10):
    #note that max output is 10 anyway
    
    preds = dl_preds(algo, usrId)
    rated = user_rated(usrId)
    
    #preds['rank'] = preds.index + 1         May use this, but index is fine
    
    mask = preds.movieId.isin(rated.movieId)  
    masked = preds[mask]
    
    display(masked)
    return mask.sum()
    
    
    

In [90]:
ratings.columns

Index(['userId', 'movieId', 'rating', 'timestamp'], dtype='object')

In [91]:
tfrs = [adamModel, adaModel]
dlmods = ['adamModel', 'adaModel']

In [ ]:
#This sometimes fails. Might want to break it up
surprise_HR = []
dl_HR = []

for usr in ratings.userId.unique():
    for algo in algos:
        print(pickles[algos.index(algo)][:-4])
        output = algo_hitrate(algo, usr)
        #print(output)
        surprise_HR.append(output)
    for dl in tfrs:
        print(dlmods[tfrs.index(dl)])
        hitrate = dl_hitrate(dl, usr)
        dl_HR.append(hitrate)
  

SVD_one_to_five


uid   iid  est  movieId_x                      title  rank  userId  \
0    1  3578  5.0       3578           Gladiator (2000)  10.5       1   
1    1  1208  5.0       1208      Apocalypse Now (1979)  10.5       1   
2    1  1278  5.0       1278  Young Frankenstein (1974)  10.5       1   

   movieId_y  rating  
0       3578     5.0  
1       1208     4.0  
2       1278     5.0

SVD_negone_to_one


uid   iid  est  movieId_x                         title  rank  userId  \
0    1     1  1.0          1              Toy Story (1995)  10.5       1   
1    1  3448  1.0       3448  Good Morning, Vietnam (1987)  10.5       1   

   movieId_y  rating  
0          1     4.0  
1       3448     5.0

SVD++_one_to_five


...

SVD_negone_to_one


uid   iid  est  movieId_x              title  rank  userId  movieId_y  \
0  369  5902  1.0       5902  Adaptation (2002)  10.5     369       5902   

   rating  
0     4.0

SVD++_one_to_five


uid   iid       est  movieId_x  \
0  369  2788  4.056131       2788   
1  369   778  4.006311        778   
2  369  2959  3.982090       2959   
3  369  1196  3.968494       1196   

                                               title  rank  userId  movieId_y  \
0  Monty Python's And Now for Something Completel...   3.0     369       2788   
1                               Trainspotting (1996)   8.0     369        778   
2                                  Fight Club (1999)  10.0     369       2959   
3  Star Wars: Episode V - The Empire Strikes Back...  13.0     369       1196   

   rating  
0     4.0  
1     4.0  
2     4.5  
3     4.0

SVD++_negone_to_one


In [ ]:
cos_HR = []
movieCF_HR = []
for usr in ratings.userId.unique():
    cos = cos_sim_hitrate(usr)
    cos_HR.append(cos)
    
    movie = movieCF_hitrate(usr)
    movieCF_HR.append(movie)


In [ ]:
pickles

In [ ]:
SVD15 = surprise_HR[::4]
SVD11 = surprise_HR[1::4]
SVDpp15 = surprise_HR[2::4]
SVDpp11 = surprise_HR[3::4]

In [ ]:
dlmods

In [ ]:
adamHR = dl_HR[::2]
adaHR = dl_HR[1::2]

In [ ]:
modelHRs = pd.DataFrame(SVD15)#, columns='SVD15')
modelHRs['SVD11'] = SVD11
modelHRs.columns = ['SVD15', 'SVD11']
modelHRs['SVDpp15'] = SVDpp15
modelHRs['SVDpp11'] = SVDpp11
modelHRs['adam'] = adamHR
modelHRs['ada'] = adaHR
modelHRs['cosSim'] = cos_HR
modelHRs['movieCF'] = movieCF_HR

In [ ]:
#modelHRs.to_csv('../../Data/hitratesAt20.csv')

In [92]:
modelHRs = pd.read_csv('../../Data/hitratesAt20.csv', index_col=[0])

In [93]:
modelHRs.describe()

SVD15       SVD11     SVDpp15     SVDpp11        adam         ada  \
count  610.000000  610.000000  610.000000  610.000000  610.000000  610.000000   
mean     5.091803    2.378689    3.940984    1.880328    0.837705    0.893443   
std      4.731000    3.163192    4.188473    2.868853    1.500374    1.589205   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      1.000000    0.000000    1.000000    0.000000    0.000000    0.000000   
50%      4.000000    1.000000    2.000000    1.000000    0.000000    0.000000   
75%      7.000000    3.000000    6.000000    2.000000    1.000000    1.000000   
max     20.000000   17.000000   20.000000   18.000000   10.000000   10.000000   

           cosSim     movieCF  
count  610.000000  610.000000  
mean     1.824590    2.257377  
std      1.681656    3.295664  
min      1.000000    0.000000  
25%      1.000000    0.000000  
50%      1.000000    1.000000  
75%      2.000000    3.000000  
max     14.000000   17.000000

In [94]:
#Now need to properly compare...
#First: compare HR
#Second: make some other metrics beyond HR (diversity)
#Third: test algorithms by hand
#Fourth: Complete study

In [95]:
#test diversity
#test popularity

In [96]:
user_div = pd.read_csv('../../Data/user_diversity.csv', index_col=[0])
movie_div = pd.read_csv('../../Data/movie_diversity.csv', index_col=[0])

In [97]:
def cos_sim_diversity(usrId, limit:int=20):
    preds = pd.DataFrame(cos_sim_preds(usrId)[:limit])
    preds = preds.merge(movie_div, left_on=preds.index, right_on=movie_div.movieId)
    
    outputRow = pd.DataFrame(preds.diversity_score.describe()).T
    
    return outputRow
    
def movieCF_diversity(usrId, limit:int=20):
    preds = movieCF_preds(usrId)[:limit]
    preds = preds.merge(movie_div, on='movieId')
    
    outputRow = pd.DataFrame(preds.diversity_score.describe()).T
    
    return outputRow

def algo_diversity(algo, usrId, limit:int=20):
    preds = algo_preds(algo, usrId)[:limit]
    preds = preds.merge(movie_div, on='movieId')
    
    outputRow = pd.DataFrame(preds.diversity_score.describe()).T
    
    return outputRow
    
def dl_diversity(algo, usrId, limit:int=20):
    preds = dl_preds(algo, usrId)[:limit]
    preds = preds.merge(movie_div, on='movieId')
    
    outputRow = pd.DataFrame(preds.diversity_score.describe()).T
    
    return outputRow

In [98]:
surprise_div = []
dl_div = []
sim_div = []
movieCF_div = [] 

tfrs = [adamModel, adaModel]
dlmods = ['adamModel', 'adaModel']

for usr in ratings.userId.unique():
    lim = 20
    
    simdiv = cos_sim_diversity(usr, lim)
    sim_div.append(simdiv)
    
    CFdiv = movieCF_diversity(usr, lim)
    movieCF_div.append(CFdiv)
    
    for algo in algos:
        print(pickles[algos.index(algo)][:-4])
        algodiv = algo_diversity(algo, usr, lim)
        #print(output)
        surprise_div.append(algodiv)
        
    for dl in tfrs:
        print(dlmods[tfrs.index(dl)])
        dldiv = dl_diversity(dl, usr, lim)
        dl_div.append(dldiv)

SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel


adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel


adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


...

adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel


adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel


adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel
SVD_one_to_five
SVD_negone_to_one
SVD++_one_to_five
SVD++_negone_to_one
adamModel
adaModel


In [99]:
def diversity_handling(input_list:list):
    for item in input_list:
        df = pd.DataFrame(item[0])
        for i in range(1, len(item)):
            df = df.append(item[i])
    return df

In [100]:
SVD15div = surprise_div[::4]
SVD11div = surprise_div[1::4]
SVDpp15div = surprise_div[2::4]
SVDpp11div = surprise_div[3::4]


In [101]:
adamdiv = dl_div[::2]
adadiv = dl_div[1::2]

In [102]:
sim_div_df = diversity_handling([sim_div])
adam_div_df = diversity_handling([adamdiv])
ada_div_df = diversity_handling([adadiv])
movieCD_div_df = diversity_handling([movieCF_div])
SVD15divDF = diversity_handling([SVD15div])
SVD11divDF = diversity_handling([SVD11div])
SVDpp15divDF = diversity_handling([SVDpp15div])
SVDpp11divDF = diversity_handling([SVDpp11div])


In [103]:
dfs = [sim_div_df, adam_div_df, ada_div_df, movieCD_div_df, SVD15divDF, SVD11divDF, SVDpp15divDF, SVDpp11divDF]
dfnames = ['sim_div_df', 'adam_div_df', 'ada_div_df', 'movieCD_div_df', 'SVD15divDF', 'SVD11divDF', 'SVDpp15divDF', 'SVDpp11divDF']

In [104]:
#Average number of genres (Diversity)
for i in range(len(dfs)):
    display(dfnames[i]+'  mean: '+str(dfs[i].describe().iloc[1,1]))
    display(dfnames[i]+' stddev: '+str(dfs[i].describe().iloc[2,1]))

'sim_div_df  mean: 2.296065573770492'

'sim_div_df stddev: 0.3422147449389217'

'adam_div_df  mean: 2.6088320559222216'

'adam_div_df stddev: 0.3788776176241522'

'ada_div_df  mean: 2.6343436117616514'

...

'SVD11divDF stddev: 0.2507457986565097'

'SVDpp15divDF  mean: 2.5750819672131153'

'SVDpp15divDF stddev: 0.220095687138446'

'SVDpp11divDF  mean: 2.5513114754098387'

'SVDpp11divDF stddev: 0.2384058675195942'

In [105]:
movie_div.columns

Index(['movieId', 'diversity_score'], dtype='object')

In [106]:
#Max number of genres (Coverage)
print('Max Genres: '+str(movie_div.diversity_score.max()))
for i in range(len(dfs)):
    display(dfnames[i]+' '+str(dfs[i].describe().iloc[-1,-1]))
    
#So this happens to mean that some movies are never recommended!

Max Genres: 10


'sim_div_df 8.0'

'adam_div_df 6.0'

'ada_div_df 6.0'

'movieCD_div_df 7.0'

'SVD15divDF 7.0'

'SVD11divDF 7.0'

'SVDpp15divDF 7.0'

'SVDpp11divDF 7.0'

In [107]:
#preds popularity rating

In [108]:
popularityTable.columns = ['movieId', 'popularity', 'title', 'ranks']


In [109]:
popRatings.tail()

rating  ranks                                   title
movieId                                                       
118894      5.0    200      Scooby-Doo! Abracadabra-Doo (2010)
99          5.0    201    Heidi Fleiss: Hollywood Madam (1995)
72142       5.0    202  Love Exposure (Ai No Mukidashi) (2008)
173351      5.0    204             Wow! A Talking Fish! (1983)
47736       5.0      1               Chump at Oxford, A (1940)

In [110]:
popularityTable

movieId  popularity                                   title  ranks
314       356         329                     Forrest Gump (1994)      1
277       318         317        Shawshank Redemption, The (1994)      2
257       296         307                     Pulp Fiction (1994)      3
510       593         279        Silence of the Lambs, The (1991)      4
1938     2571         278                      Matrix, The (1999)      5
...       ...         ...                                     ...    ...
3053     4093           1                              Cop (1988)   9718
3049     4089           1                Born in East L.A. (1987)   9719
6686    58351           1  City of Men (Cidade dos Homens) (2007)   9720
3045     4083           1                      Best Seller (1987)   9721
9721   193609           1     Andrew Dice Clay: Dice Rules (1991)   9722

[9722 rows x 4 columns]

In [111]:
pd.DataFrame(cos_sim_preds(80))[:20]#.merge(popularityTable[['movieId', 'ranks']], on='movieId').ranks.mean()

8810
8810   1.0
8815   1.0
8617   1.0
8813   1.0
8800   1.0
8814   1.0
8795   1.0
8808   1.0
8807   1.0
8809   1.0
8620   1.0
8626   1.0
8798   1.0
8799   1.0
8743   1.0
8507   1.0
8830   1.0
8831   1.0
8690   1.0
8833   1.0

In [112]:
def cos_sim_pop(usrId, limit:int=20):
    popularity = []
    for usr in usrId:
        preds = pd.DataFrame(cos_sim_preds(usr)[:limit])
        preds = preds.merge(popularityTable[['movieId', 'ranks']], 
                            left_on=preds.index, right_on=popularityTable.movieId)

        popularity.append(preds.ranks.mean())  

    return np.mean(popularity)

In [113]:
def movieCF_pop(usrId, limit:int=20):
    popularity = []
    for usr in usrId:
        preds = movieCF_preds(usr)[:limit]
        preds = preds.merge(popularityTable[['movieId', 'ranks']], on='movieId')

        popularity.append(preds.ranks.mean())  

    return np.mean(popularity)

def algo_pop(algo, usrId, limit:int=20):
    popularity = []
    for usr in usrId:
        preds = algo_preds(algo, usr)[:limit]
        preds = preds.merge(popularityTable[['movieId', 'ranks']], on='movieId')

        popularity.append(preds.ranks.mean())  

    return np.mean(popularity)

def dl_pop(algo, usrId, limit:int=20):
    popularity = []
    for usr in usrId:
        preds = dl_preds(algo, usr)[:limit]
        preds = preds.merge(popularityTable[['movieId', 'ranks']], on='movieId')

        popularity.append(preds.ranks.mean())  

    return np.mean(popularity)

In [114]:
cos_sim_pop([id for id in ratings.userId.unique()])

4220.684935289043

In [115]:
movieCF_pop([id for id in ratings.userId.unique()])

2052.8152459016396

In [116]:
lim=20

In [117]:
for algo in algos:
    print(pickles[algos.index(algo)][:-4])
    print(algo_pop(algo, [id for id in ratings.userId.unique()], lim))      


SVD_one_to_five
379.79754098360655
SVD_negone_to_one
928.1754098360656
SVD++_one_to_five
715.7404918032787
SVD++_negone_to_one
1080.8074590163935


In [118]:
for dl in tfrs:
    print(dlmods[tfrs.index(dl)])
    print(dl_pop(dl, [id for id in ratings.userId.unique()], lim))


adamModel
1023.5992703380407
adaModel
651.3901632838928


In [119]:
#Performance of SVDpp considerably worse
#SVD15 basically best in every way
#ada is better DL model